In [ ]:
# @title ⚄ 🔄 Initialize

import os
home_directory = '/content/'
using_Kaggle = os.environ.get('KAGGLE_URL_BASE','')
if using_Kaggle : home_directory = '/kaggle/working/'
%cd {home_directory}

def fix_bad_symbols(txt):
  result = txt
  for symbol in ['^', '}', '{' , ')', '(', '[' , ']' , ':' , '=' ]:
    result = result.replace(symbol,'\\' + symbol)
  #------#
  return result;

def my_mkdirs(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)

#🔸🔹
# Load the data if not already loaded
try:
    loaded
except:
  from safetensors.torch import load_file , save_file
  import json , torch , requests , math
  import pandas as pd
  from PIL import Image
  import cv2
  from matplotlib import pyplot as plt
  #----#
  %cd {home_directory}
  !git clone https://huggingface.co/datasets/codeShare/fusion-t2i-generator-data
  loaded = True
  %cd {home_directory + 'fusion-t2i-generator-data/'}
  !unzip reference.zip

from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-large-patch14", clean_up_tokenization_spaces = False)
from transformers import  CLIPProcessor, CLIPModel
processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14" , clean_up_tokenization_spaces = True)
model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
logit_scale = model.logit_scale.exp() #logit_scale = 100.00000762939453

#------#
%cd {home_directory + 'fusion-t2i-generator-data/' + 'reference'}
with open(f'reference_prompts.json', 'r') as f:
  data = json.load(f)
  _df = pd.DataFrame({'count': data})['count']
  target_prompts = {
      key : value for key, value in _df.items()
  }
#------#
with open(f'reference_urls.json', 'r') as f:
  data = json.load(f)
  _df = pd.DataFrame({'count': data})['count']
  target_urls = {
      key : value for key, value in _df.items()
  }

#------#
dot_dtype = torch.float32
dim = 768
ref = torch.zeros(dim).to(dtype = dot_dtype)

# title ⚄  Define parameters for visalizing the reference in a 16x16 grid <br> (the visualization settings has no effect on output)
from PIL import Image, ImageDraw
SCALE = 0.0002 # param {type:"slider", min:0.0001, max:0.001, step:0.00001}
ZERO_POINT = 100 # param {type:"slider", min:0, max:300, step:1}
CELL_SIZE = 16
image_size = 0.5 # param {type:"slider", min:0, max:1, step:0.01}
show_encoding = False # param {type:"boolean"}
#------#

BORDER_THICKNESS = 4

def visualize(_ref):
  RGB_tensor = (torch.round(_ref/SCALE)+torch.ones(dim)*ZERO_POINT)
  cellsize = CELL_SIZE
  tick = round(cellsize/2)
  border_offset = round(BORDER_THICKNESS/2)
  width = 16*cellsize + BORDER_THICKNESS
  height = 16*cellsize + BORDER_THICKNESS
  image = Image.new('RGB', (width, height), (0, 0, 0))
  draw = ImageDraw.Draw(image)
  for row in range(16):
    for col in range(16):
      tmp = 3*row*col
      r = max(0,min(255,int(RGB_tensor[tmp].item())))
      g = max(0,min(255,int(RGB_tensor[tmp+1].item())))
      b = max(0,min(255,int(RGB_tensor[tmp+2].item())))
      fillColor = (r,g,b)
      x0 = row*cellsize +border_offset
      y0 = (15-col)*cellsize +border_offset
      x1 = row*cellsize + 2*tick + border_offset
      y1 = (15-col)*cellsize + 2*tick + border_offset
      shape = [(x0, y0), (x1, y1)]
      draw.rectangle(shape, fill=fillColor, outline=(0,0,0))
  return (image)

num_plots = 1
try:
  %cd /content/
  _ref = load_file('reference.safetensors' )
  num_plots = num_plots+1
except: _ref = torch.zeros(dim).to(dtype = dot_dtype)
#-----#
try: ref
except: ref =  torch.zeros(dim).to(dtype = dot_dtype)


if show_encoding:
  # create figure
  fig = plt.figure(figsize=(10*image_size, 10*image_size))
  fig.patch.set_facecolor((56/255,56/255,56/255))
  rows = 1
  columns = num_plots
  fig.add_subplot(rows, columns, 1)
  plt.imshow( visualize(ref))
  plt.axis('off')
  plt.title( "Encoding (local variable)",  color='white',  fontsize=round(20*image_size))
  if num_plots>1:
    fig.add_subplot(rows, columns, 2)
    plt.imshow( visualize( _ref['weights'].to(dot_dtype)))
    plt.axis('off')
    plt.title("Encoding (saved file)",  color='white',  fontsize=round(20*image_size))
  #------#

print(f'Using settings SCALE = {SCALE} and ZERO_POINT = {ZERO_POINT} for visualizing the text_encoding')

In [ ]:
# @title ⚄ 📷💭 Use pre-encoded image+prompt pair
loaded_ref = False
try:
  ref
  loaded_ref = True
except:ref = torch.zeros(dim).to(dtype = dot_dtype)
if loaded_ref : prev_ref = ref.clone().detach()

try:prompt
except: prompt = ''

# @markdown 🖼️+📝 Choose a pre-encoded reference (note: some results are NSFW!)
index = 596 # @param {type:"slider", min:0, max:1666, step:1}
PROMPT_INDEX = index
prompt = target_prompts[f'{PROMPT_INDEX}']
url = target_urls[f'{PROMPT_INDEX}']
if url.find('perchance')>-1:
  image = Image.open(requests.get(url, stream=True).raw)
#------#
%cd {home_directory + 'fusion-t2i-generator-data/' + 'reference'}
references = torch.load('reference_text_and_image_encodings.pt'  , weights_only=False)
# @markdown ⚖️ 🖼️ encoding <-----?-----> 📝 encoding </div> <br>
C = 0.3 # @param {type:"slider", min:0, max:1, step:0.01}
log_strength = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
method = 'Add to existing ref' # @param ["Refresh" , "Add to existing ref" , "Subtract from existing ref" , "Do nothing"]
image_size = 0.57 # @param {type:"slider", min:0, max:1, step:0.01}
show_encoding = True # @param {type:"boolean"}

if(not method == 'Do nothing'):
  if method == 'Refresh': ref = torch.zeros(dim).to(dtype = dot_dtype)
  if method == 'Subtract from existing ref':
    ref = torch.sub(ref, math.pow(10 ,log_strength-1) * C * references[index][0].dequantize().to(dtype = torch.float32))
    ref = torch.sub(ref, math.pow(10 ,log_strength-1) * (1-C) * references[index][1].dequantize().to(dtype = torch.float32))
  else:
    ref = torch.add(ref, math.pow(10 ,log_strength-1) * C * references[index][0].dequantize().to(dtype = torch.float32))
    ref = torch.add(ref, math.pow(10 ,log_strength-1) * (1-C) * references[index][1].dequantize().to(dtype = torch.float32))
  #---------#
  references = '' # Clear up memory
  ref = ref/ref.norm(p=2, dim=-1, keepdim=True)
  ref = ref.clone().detach()
  #------#
  # create figure
  fig = plt.figure(figsize=(10*image_size, 10*image_size))
  fig.patch.set_facecolor((56/255,56/255,56/255))
  rows = 1
  columns = 1
  if show_encoding: columns = columns+1
  if show_encoding and loaded_ref : columns = columns+1
  fig.add_subplot(rows, columns, 1)
  plt.imshow(image)
  plt.axis('off')
  plt.title(f"Reference image at index={index}" ,  color='white' , fontsize=round(20*image_size))
  #-----#
  if show_encoding and loaded_ref:
    fig.add_subplot(rows, columns, columns-1)
    plt.imshow( visualize(prev_ref))
    plt.axis('off')
    plt.title("Encoding (before)" ,  color='white' , fontsize=round(20*image_size))
  print(f'Prompt for this image : \n\n "{prompt} " \n\n')

  if show_encoding:
    fig.add_subplot(rows, columns, columns)
    plt.imshow( visualize(ref))
    plt.axis('off')
    plt.title("Encoding (now)" ,  color='white' , fontsize=round(20*image_size))
  #------#


# Other methods

In [ ]:
# @title ⚄ 🧩 Create an encoding
# @markdown 📝 Write a text prompt (this will overwrite any savefile already stored)
NEW_ENCODING = '' # @param {type:'string' ,placeholder:'write a prompt'}
enable = True # @param {type:"boolean"}
# @markdown -----
# @markdown 📝 Enhance/Penalize Similarity and skip items containing word(s)
POS = '' # @param {type:'string' ,placeholder:'item1 , item2 , ...'}
NEG = ''# @param {type:'string' ,placeholder:'item1 , item2 , ...'}
# @markdown -----
# @markdown logarithmic prompt strength x for value 10^(x-1)
_POS = 0 # @param {type:"slider", min:-5, max:5, step:0.01}
_NEG = 0  # @param {type:"slider", min:-5, max:5, step:0.01}
# @markdown -----
# @markdown Check similiarity for this encoding against any written prompt(s)
# @title ⚄ Evaluate saved  reference similarity to select items (optional)
EVAL = '' # @param {type:'string' ,placeholder:'item1 , item2 , ...'}

show_local_reference = True # @param {type:"boolean"}
show_encoding = True # @param {type:"boolean"}

try:
  %cd /content/
  _ref = load_file('reference.safetensors' )
  ref = _ref['weights'].to(dot_dtype)
except:
  ref = torch.zeros(dim).to(dtype = dot_dtype)
  _ref = {}
  _ref['weights'] = ref
  %cd /content/
  save_file(_ref, 'reference.safetensors')
#-----#

if NEW_ENCODING.strip() != '':
  item = NEW_ENCODING.strip()
  inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
  ref = model.get_text_features(**inputs)[0]
  ref= ref/ref.norm(p=2 , dim=-1 , keepdim=True)
#------#

try: ref
except: ref = torch.zeros(dim).to(dtype = dot_dtype)

if EVAL.strip() != '':
  print("Saved Reference:\n")
  for item in EVAL.split(','):
    if item.strip()=='':continue
    inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
    test = model.get_text_features(**inputs)[0]
    test = test/test.norm(p=2 , dim = -1 , keepdim = True)
    ref= ref/ref.norm(p=2 , dim=-1 , keepdim=True)
    eval = torch.dot(ref , test)
    print(f'{item.strip()} : {round(eval.item()*100, 2)}%')
  #-----#
  if(show_local_reference):
    print("\n---------\nLocal Reference with enchancements added :\n")

    for _item in POS.split(','):
      item = _item.strip()
      if item == '':continue
      inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
      ref = ref + math.pow(10,_POS-1) * model.get_text_features(**inputs)[0]
    #-------#

    for _item in NEG.split(','):
      item = _item.strip()
      if item == '':continue
      inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
      ref = ref + math.pow(10,_NEG-1) * model.get_text_features(**inputs)[0]
    #-------#

    ref= ref/ref.norm(p=2 , dim=-1 , keepdim=True)
    for item in EVAL.split(','):
      if item.strip()=='':continue
      inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
      test = model.get_text_features(**inputs)[0]
      test = test/test.norm(p=2 , dim = -1 , keepdim = True)
      eval = torch.dot(ref , test)
      print(f'{item.strip()} : {round(eval.item()*100, 2)}%')
    #-----#

  if show_encoding:
    # create figure
    fig = plt.figure(figsize=(10*image_size, 10*image_size))
    fig.patch.set_facecolor((56/255,56/255,56/255))
    rows = 1
    columns = 3
    fig.add_subplot(rows, columns, 1)
    plt.imshow( visualize(ref))
    plt.axis('off')
    plt.title( "Encoding (local variable)",  color='white',  fontsize=round(20*image_size))
    if num_plots>1:
      fig.add_subplot(rows, columns, 2)
      plt.imshow( visualize( _ref['weights'].to(dot_dtype)))
      plt.axis('off')
      plt.title("Encoding (saved file)",  color='white',  fontsize=round(20*image_size))

      fig.add_subplot(rows, columns, 3)
      plt.imshow( visualize(ref - _ref['weights'].to(dot_dtype)))
      plt.axis('off')
      plt.title("Changes",  color='white',  fontsize=round(20*image_size))
    #------#




**Use an image as a reference via URL (optional)**

In [ ]:
# @title ⚄ 🌐🖼️ Load an image via URL
loaded_ref = False
try:
  ref
  loaded_ref = True
except:ref = torch.zeros(dim).to(dtype = dot_dtype)
if loaded_ref : prev_ref = ref.clone().detach()

try:prompt
except: prompt = ''

# @markdown 🖼️ Upload your own image for use as reference via URL (optional)
URL = '' # @param {type:'string' ,placeholder:'paste an url here'}
if URL.strip() != '':
  image = Image.open(requests.get(URL, stream=True).raw)
  log_strength = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
  method = 'Add to existing ref' # @param ["Refresh" , "Add to existing ref" , "Subtract from existing ref" , "Do nothing"]
  image_size = 0.79 # @param {type:"slider", min:0, max:1, step:0.01}
  show_encoding = True # @param {type:"boolean"}
  #---------#
  if(not method == 'Do nothing'):
    # Get image features
    inputs = processor(images=image, return_tensors="pt")
    image_features = model.get_image_features(**inputs)
    image_features = image_features / image_features.norm(p=2, dim=-1, keepdim=True)
    #-------#
    if method == 'Refresh':
      ref = torch.zeros(dim).to(dtype = dot_dtype)
    if method == 'Subtract from existing ref':
      ref = ref - math.pow(10,log_strength-1)*image_features
    else: ref = ref + math.pow(10,log_strength-1)*image_features
    #-----#
    ref = ref/ref.norm(p=2, dim=-1, keepdim=True)
    ref = ref[0]
    ref = ref.clone().detach()
    #------#
    # create figure
    fig = plt.figure(figsize=(10*image_size, 10*image_size))
    fig.patch.set_facecolor((56/255,56/255,56/255))
    rows = 1
    columns = 1
    if show_encoding: columns = 2
    if show_encoding and loaded_ref : columns = 3
    fig.add_subplot(rows, columns, 1)
    plt.imshow(image)
    plt.axis('off')
    plt.title("Reference image from URL" ,  color='white' , fontsize=round(20*image_size))
    #-----#
    if show_encoding and loaded_ref:
      fig.add_subplot(rows, columns, columns-1)
      plt.imshow( visualize(prev_ref))
      plt.axis('off')
      plt.title("Encoding (before)" ,  color='white' , fontsize=round(20*image_size))
    if show_encoding:
      fig.add_subplot(rows, columns, columns)
      plt.imshow( visualize(ref))
      plt.axis('off')
      plt.title("Encoding (now)" ,  color='white' , fontsize=round(20*image_size))
    #------#

**Use an image as a reference via uploading it to the /content/ folder (optional)**

In [ ]:
# @title ⚄ 📂🖼️ Use an uploaded image as reference
loaded_ref = False
try:
  ref
  loaded_ref = True
except:ref = torch.zeros(dim).to(dtype = dot_dtype)
if loaded_ref : prev_ref = ref.clone().detach()

try:prompt
except: prompt = ''

# @markdown 🖼️ Upload your own image for use as reference via URL (optional)
FILENAME = '' # @param {type:'string' ,placeholder:'IMG_123.png'}
log_strength = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
method = 'Add to existing ref' # @param ["Refresh" , "Add to existing ref" , "Subtract from existing ref" , "Do nothing"]
image_size = 0.5 # @param {type:"slider", min:0, max:1, step:0.01}
show_encoding = True # @param {type:"boolean"}

if FILENAME.strip() != '':
  %cd /content/
  image = cv2.imread(FILENAME)
  b,g,r = cv2.split(image)
  image = cv2.merge([r,g,b])
  #---------#
  if(not method == 'Do nothing'):
    # Get image features
    inputs = processor(images=image, return_tensors="pt")
    image_features = model.get_image_features(**inputs)
    image_features = image_features / image_features.norm(p=2, dim=-1, keepdim=True)
    #-------#
    if method == 'Refresh':
      ref = torch.zeros(dim).to(dtype = dot_dtype)
    if method == 'Subtract from existing ref':
      ref = ref - math.pow(10,log_strength-1)*image_features
    else: ref = ref + math.pow(10,log_strength-1)*image_features
    #-----#
    ref = ref/ref.norm(p=2, dim=-1, keepdim=True)
    ref = ref[0]
    ref = ref.clone().detach()
    #------#
    # create figure
    fig = plt.figure(figsize=(10*image_size, 10*image_size))
    fig.patch.set_facecolor((56/255,56/255,56/255))
    rows = 1
    columns = 1
    if show_encoding: columns = 2
    if show_encoding and loaded_ref : columns = 3
    fig.add_subplot(rows, columns, 1)
    plt.imshow(image)
    plt.axis('off')
    plt.title(f"Reference image from uploaded image {FILENAME}" ,  color='white' , fontsize=round(20*image_size))
    #-----#
    if show_encoding and loaded_ref:
      fig.add_subplot(rows, columns, columns-1)
      plt.imshow( visualize(prev_ref))
      plt.axis('off')
      plt.title("Encoding (before)" ,  color='white' , fontsize=round(20*image_size))
    if show_encoding:
      fig.add_subplot(rows, columns, columns)
      plt.imshow( visualize(ref))
      plt.axis('off')
      plt.title("Encoding (now)" ,  color='white' , fontsize=round(20*image_size))
    #------#

# Search prompts using CLIP

In [ ]:
# @title ⚄ 💾 Save the reference

loaded_ref = False
try:
  ref
  loaded_ref = True
except:ref = torch.zeros(dim).to(dtype = dot_dtype)
if loaded_ref : prev_ref = ref.clone().detach()

try:prompt
except: prompt = ''

reset_everything = False # @param {type:"boolean"}
_ref = {}
ref = ref/ref.norm(p=2, dim=-1, keepdim=True)
if (reset_everything) : ref = torch.zeros(dim).to(dtype = dot_dtype)
_ref['weights'] = ref.to(dot_dtype)
%cd /content/
save_file(_ref , 'reference.safetensors' )
image_size = 0.5 # @param {type:"slider", min:0, max:1, step:0.01}
show_encoding = True # @param {type:"boolean"}
#------#
print("Saved local encoding to reference.safetensors")
if show_encoding:
  # create figure
  fig = plt.figure(figsize=(10*image_size, 10*image_size))
  fig.patch.set_facecolor((56/255,56/255,56/255))
  rows = 1
  columns = num_plots
  fig.add_subplot(rows, columns, 1)
  plt.imshow( visualize(ref))
  plt.axis('off')
  plt.title( "Encoding (local variable)",  color='white',  fontsize=round(20*image_size))
  if num_plots>1:
    fig.add_subplot(rows, columns, 2)
    plt.imshow( visualize( _ref['weights'].to(dot_dtype)))
    plt.axis('off')
    plt.title("Encoding (saved file)",  color='white',  fontsize=round(20*image_size))
  #------#

**Run the interrogator**

 Since the list of items is large (>1 million items) you will need to select a range within the sorted results to print.

In [ ]:
# @title ⚄ 🕵️‍♂️ Run the CLIP Interrogator
LIST_SIZE = 1000  # @param {type:'number' , placeholder:'set how large the list should be'}
_START_AT = '0' # @param ["0", "10000", "50000"] {allow-input: true}
START_AT = 0
#-----#
if _START_AT.find('K')>-1:
  START_AT = _START_AT.replace('K','')
  if START_AT.isnumeric(): START_AT = int(START_AT)*1000
#------#
else:
  if _START_AT.isnumeric(): START_AT = int(_START_AT)
#----#

output_folder = home_directory + 'results/'
output_folder_sims = home_directory + 'results/sims/'
my_mkdirs(output_folder)
my_mkdirs(output_folder_sims)

# @markdown -----
# @markdown Select vocab
general = True # @param {type:"boolean"}
civit9 = True # @param {type:"boolean"}
fanfic1 = False # @param {type:"boolean"}
fanfic2 = False # @param {type:"boolean"}
# @markdown -----
# @title ⚄ New interrogator code using quantized text corpus
%cd /content/
_ref = load_file('reference.safetensors' )
ref = _ref['weights'].to(dot_dtype)
# @markdown 📝 Enhance/Penalize Similarity and skip items containing word(s)
POS1 = '' # @param {type:'string' ,placeholder:'item1 , item2 , ...'}
POS2 = '' # @param {type:'string' ,placeholder:'item1 , item2 , ...'}
NEG = ''# @param {type:'string' ,placeholder:'item1 , item2 , ...'}
SKIP = '' # @param {type:'string' ,placeholder:'item1 , item2 , ...'}
min_wordcount = 0 # @param {type:"slider", min:0, max:20, step:1}
def isBlacklisted(_txt):
  blacklist =  SKIP.lower().replace('</w>' , ' ').replace('{' , '').replace('}' , '').replace('|' , ',').strip()
  if blacklist == '': return False
  txt = _txt.lower().strip()
  if len(txt)<min_wordcount: return True
  if txt.isnumeric(): return True
  #-----#
  for item in list(blacklist.split(',')):
    if item.strip() == '' : continue
    if txt.find(item.strip())> -1 : return True
  #------#
  found = False
  alphabet = 'abcdefghijklmnopqrstuvxyz'
  for letter in alphabet:
    found =  txt.find(letter)>-1
    if found:break
  #------#
  return not found
# @markdown -----
# @markdown logarithmic prompt strength x for value 10^(x-1)
_POS1 = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
_POS2 = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
_NEG = 1 # @param {type:"slider", min:-5, max:5, step:0.01}
# @markdown -----
# @markdown Save similarity as a list for later review (this will slow down the code)
save_similiarity = True # @param {type:"boolean"}
# @markdown -----
include_similiarity = False # @param {type:"boolean"}
print_as_list = False # @param {type:"boolean"}
N = 7 # @param {type:"slider", min:0, max:10, step:1}
#-----#
for _item in POS1.split(','):
  item = _item.strip()
  if item == '':continue
  inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
  ref = ref + math.pow(10,_POS1-1) * model.get_text_features(**inputs)[0]
#-------#
for _item in POS2.split(','):
  item = _item.strip()
  if item == '':continue
  inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
  ref = ref + math.pow(10,_POS2-1) * model.get_text_features(**inputs)[0]
#-------#
for _item in NEG.split(','):
  item = _item.strip()
  if item == '':continue
  inputs = tokenizer(text = item.strip(), truncation = True  , padding=True, return_tensors="pt")
  ref = ref + math.pow(10,_NEG-1) * model.get_text_features(**inputs)[0]
#------#
ref = (ref/ref.norm(p=2, dim=-1, keepdim=True)).to(dtype = dot_dtype)
vocab_to_load = ''
if (general): vocab_to_load = vocab_to_load + 'general , '
if (civit9): vocab_to_load = vocab_to_load + 'civit9 , '
if (fanfic1): vocab_to_load = vocab_to_load + 'fanfic1 , '
if (fanfic2): vocab_to_load = vocab_to_load + 'fanfic2 , '
vocab_to_load = (vocab_to_load +'}').replace(' , }' , '')
multi = vocab_to_load.find(',')>-1
#-----#
prompts_folder = f'{home_directory}fusion-t2i-generator-data/vocab-v2/text'
encodings_folder = f'{home_directory}fusion-t2i-generator-data/vocab-v2/text_encodings'
#----#
scale = 0.0043
size = 0
#------#
total_items = 0
for filename in os.listdir(prompts_folder):
  if (not general and filename.find('general')>-1):continue
  if (not civit9 and filename.find('civit9')>-1):continue
  if (not fanfic1 and filename.find('fanfic1')>-1):continue
  if (not fanfic2 and filename.find('fanfic2')>-1):continue
  size = size + LIST_SIZE
#-------#
similiar_sims = torch.zeros(size)
similiar_prompts = {}
_index = 0
#-------#
similiar_encodings = {}
for filename in os.listdir(prompts_folder):
  if (not general and filename.find('general')>-1):continue
  if (not civit9 and filename.find('civit9')>-1):continue
  if (not fanfic1 and filename.find('fanfic1')>-1):continue
  if (not fanfic2 and filename.find('fanfic2')>-1):continue
  #------#
  root_filename = filename.replace('.json', '')
  %cd {prompts_folder}
  prompts = {}
  with open(f'{root_filename}.json', 'r') as f:
    data = json.load(f).items()
    for key,value in data:
      prompts[key] = value
  num_items = int(prompts['num_items'])
  total_items = total_items + num_items
  #------#
  try:vocab_loaded
  except:
    vocab_loaded = 'first'
  #-----#
  if  vocab_loaded == 'first' or (vocab_loaded != vocab_to_load and not multi):
    %cd {encodings_folder}
    _text_encodings = load_file(f'{root_filename}.safetensors')['weights'].to(torch.uint8)
    text_encodings = torch.zeros(num_items , dim)
    tmp = torch.ones(dim).to(dot_dtype)
    for index in range(num_items):
      text_encodings[index] = torch.sub(_text_encodings[index][1:dim+1].to(dot_dtype) , tmp , alpha= _text_encodings[index][0].to(dot_dtype))
    vocab_loaded = vocab_to_load
  #------#
  sims = torch.matmul(text_encodings*scale, ref.t())
  sorted , indices = torch.sort(sims , dim=0 , descending = True)
  tmp = {}
  tmp['weights'] = sorted
  %cd {output_folder_sims}
  save_file(tmp, root_filename + '_sims.safetensors')
  tmp={}
  #-----#
  for index in range(LIST_SIZE + START_AT):
    if index<START_AT: continue
    key = indices[index].item()
    try:prompt = prompts[f'{key}']
    except:continue
    if(isBlacklisted(prompt)):continue
    #-------#
    similiar_sims[_index] = torch.tensor(round(sims[key].item(), 5))
    similiar_prompts[f'{_index}'] = prompt
    _index = _index + 1
  #-------#
  continue
#---------#
total_items = total_items + num_items+1
#-------#
print(f'\nProcessed entire list of {total_items} items to find closest match.\nSaved closest matching indices {START_AT} to {START_AT + LIST_SIZE} as the dict "similiar_prompts" with {LIST_SIZE} items.\n')

# Print results
sorted , indices = torch.sort(similiar_sims , dim=0 , descending = True)
if(print_as_list):
  for index in range(LIST_SIZE):
    key = indices[index].item()
    sim = similiar_sims[key].item()
    prompt = similiar_prompts[f'{key}']
    if include_similiarity :print(f'{prompt}  - {round(sim*100,1)} %')
    else: print(f'{prompt}')
#-------#
else:
  prompt = ''
  for iter in range(N):
    prompt = prompt + '{'
    for index in range(LIST_SIZE):
      key = indices[index].item()
      sim = similiar_sims[key].item()
      prompt = prompt + fix_bad_symbols(similiar_prompts[f'{key}']) + '|'
    #-----#
    prompt = (prompt + '}').replace('|}',  '} ')
  #------#
  print(f'Similiar prompts: \n\n\n{prompt} \n\n\n//----//')
#-----#

#Clear memory
_text_encodings = {}
prompts = {}
#-----#

image


**Evaluate Similarities**

Run this cell to see how far down the list you can go before similarity to the reference is lost.

In [ ]:
# @title ⚄ 🔍 Test how unique the encoding is
%cd {output_folder_sims}
index = 0
for filename in os.listdir(output_folder_sims):
  _sims = load_file(filename)
  _sims = _sims['weights']
  for _sim in _sims.tolist():
    index = index + 1
  #-------#
total_items = index
sims = torch.zeros(total_items)
index = 0
for filename in os.listdir(output_folder_sims):
  _sims = load_file(filename)
  _sims = _sims['weights']
  for sim in _sims.tolist():
    sims[index] = sim
    index = index + 1
  #-------#
#---------------#
_sorted , indices  = torch.sort(sims , dim=0 , descending = True)
SCALE = 0.001
sorted = torch.round(_sorted/SCALE)
ZERO_POINT = sorted[total_items-1].item()
sorted = (sorted - torch.ones(total_items)*ZERO_POINT)
densities = torch.bincount(sorted.to(dtype = torch.int64))
yy = densities.tolist()
top = (sorted[0] + ZERO_POINT).to(dtype = torch.int64).item()
num_coords = round(top - ZERO_POINT)
xx = [round((ZERO_POINT + x)*100*SCALE,2) for x in range(num_coords+1)]
index = 0
for item in xx:
  if item>0:break
  index = index + 1
#----#
positive_bound = index
ss =list(xx)
tmp = 0
chunk = 1
CHUNK_SIZE = 1000
index = 0
for num in reversed(yy):
  tmp = tmp + num
  if(tmp>CHUNK_SIZE):
    _tmp = math.floor(tmp/CHUNK_SIZE)
    chunk = chunk + _tmp
    tmp = tmp - CHUNK_SIZE * _tmp
  ss[num_coords - index] = chunk
  index = index + 1
#------#
fig, ax = plt.subplots()
fig.canvas.draw()
plt.plot(ss[positive_bound:], xx[positive_bound:])
plt.xlabel ('Search depth')
plt.ylabel ('Similarity')
plt.title ('Similarity to index')
plt.grid()
indices_depth = [item.get_text() for item in ax.get_xticklabels()]
sim_pcnts = [item.get_text() for item in ax.get_yticklabels()]

index = 0
for index_depth in indices_depth:
  indices_depth[index] = index_depth + 'K'
  index = index + 1
#-------#

index = 0
for sim_pcnt in sim_pcnts:
  sim_pcnts[index] = sim_pcnt + '%'
  index = index + 1
#-------#
ax.set_xticklabels(indices_depth)
ax.set_yticklabels(sim_pcnts)
plt.show()

In [ ]:
# @title ⚄ Save the results

def mkdir(folder):
  if os.path.exists(folder)==False:
    os.makedirs(folder)
#-----#
output_folder = home_directory + 'results'
mkdir(output_folder)
#-----#
try: similiar_prompts
except:similiar_prompts = {}
%cd {output_folder}
print(f'Saving similiar_prompts.json to {output_folder}...')
with open('similiar_prompts.json', 'w') as f:
  json.dump(similiar_prompts, f)
#-----#
try: similiar_sims
except: similiar_sims = torch.zeros(dim).to(dot_dtype)
#-------#
_similiar_sims = {}
_similiar_sims['weights'] = similiar_sims.to(dot_dtype)
%cd {output_folder}
print(f'Saving similiar_sims.safetensors to {output_folder}...')
save_file(_similiar_sims, 'similiar_sims.safetensors')


In [ ]:

# @title ⚄ Print results
sorted , indices = torch.sort(similiar_sims , dim=0 , descending = True)
include_similiarity = False # @param {type:"boolean"}
print_as_list = False # @param {type:"boolean"}
N = 7 # @param {type:"slider", min:0, max:10, step:1}
FILENAME = '' # @param {type:'string' ,placeholder:'write .json file to load (optional)'}
_FILENAME  = FILENAME.replace('.json' , '')
if _FILENAME.strip() == '': _FILENAME = 'similiar_prompts'
#------#
%cd {output_folder}
with open(f'{_FILENAME}.json', 'r') as f:
  data = json.load(f)
  _df = pd.DataFrame({'count': data})['count']
  similiar_prompts = {
      key : value for key, value in _df.items()
  }
#-------#
_similiar_sims = load_file('similiar_sims.safetensors')
similiar_sims = _similiar_sims['weights'].to(dot_dtype)

# @title ⚄ Run the CLIP interrogator on the saved reference

# @markdown Select which values within the saved list to print
LIST_SIZE = 1000  # @param {type:'number' , placeholder:'set how large the list should be'}
START_AT = 0  # @param {type:'number' , placeholder:'set how large the list should be'}

if(print_as_list):
  for index in range(LIST_SIZE + START_AT):
    if index<START_AT:continue
    key = indices[index].item()
    sim = similiar_sims[key].item()
    prompt = similiar_prompts[f'{key}']
    if include_similiarity :print(f'{prompt}  - {round(sim*100,1)} %')
    else: print(f'{prompt}')
#-------#
else:
  prompt = ''
  for iter in range(N):
    prompt = prompt + '{'
    for index in range(LIST_SIZE + START_AT):
      if index<START_AT:continue
      key = indices[index].item()
      sim = similiar_sims[key].item()
      prompt = prompt + fix_bad_symbols(similiar_prompts[f'{key}']) + '|'
    #-----#
    prompt = (prompt + '}').replace('|}',  '} ')
  #------#
  print(f'Similiar prompts: \n\n {prompt} \n\n')
image
#-----#
